# DCGAN

Import library

In [119]:
from keras.models import Sequential
from keras.layers import Dense
from keras.layers import Reshape
from keras.layers.core import Activation
from keras.layers.normalization import BatchNormalization
from keras.layers.convolutional import UpSampling2D
from keras.layers.convolutional import Conv2D, MaxPooling2D
from keras.layers.core import Flatten
from keras.optimizers import SGD
from keras.datasets import mnist
import numpy as np
from PIL import Image
import argparse
import math
from keras import backend as K
import timeit

# Generator model

In [120]:
def generator_model():
    model = Sequential()
    model.add(Dense(1024, input_shape=(100, ), activation='tanh'))
    model.add(Dense(128 * 7 * 7))
    model.add(BatchNormalization())
    model.add(Activation('tanh'))
    model.add(Reshape((7, 7, 128), input_shape=(7 * 7 * 128,)))
    model.add(UpSampling2D(size=(2, 2)))
    model.add(Conv2D(64, (5, 5), 
                     padding='same',
                     activation='tanh',
                     data_format='channels_last'))
    model.add(UpSampling2D(size=(2, 2)))
    model.add(Conv2D(1, (5, 5), 
                     padding='same', 
                     activation='tanh',
                     data_format='channels_last'))
    return model

# Descriminator model

In [121]:
def discriminator_model():
    model = Sequential()
    model.add(Conv2D(64, (5, 5),
                    padding='same',
                    input_shape=(28, 28, 1),
                    activation='tanh',
                    data_format='channels_last'
    ))
    model.add(MaxPooling2D(pool_size=(2, 2)))
    model.add(Conv2D(128, (5, 5),
                    activation='tanh',
                    data_format='channels_last'))
    model.add(MaxPooling2D(pool_size=(2, 2)))
    model.add(Flatten())
    model.add(Dense(1024, activation='tanh'))
    model.add(Dense(1, activation='sigmoid'))
    return model

# Generator and Discriminator

In [122]:
def generator_containing_discriminator(generator, discriminator):
    model = Sequential()
    model.add(generator)
    discriminator.trainable = False
    model.add(discriminator)
    return model

# Combine image

In [ ]:
def combine_images(generated_images):
    generated_images = generated_images.reshape(generated_images.shape[0], 
                                                generated_images.shape[3], 
                                                generated_images.shape[1],
                                                generated_images.shape[2])
    num = generated_images.shape[0]
    width = int(math.sqrt(num))
    height = int(math.ceil(float(num) / width))
    shape = generated_images.shape[2:]
    image = np.zeros((height * shape[0], width * shape[1]),
                     dtype=generated_images.dtype)
    for index, img in enumerate(generated_images):
        i = int(index / width)
        j = index % width
        image[i * shape[0]:(i + 1) * shape[0], j * shape[1]:(j + 1) * shape[1]] = \
            img[0, :, :]
    return image

# Training

In [ ]:
def train(BATCH_SIZE):
    (X_train, y_train), (X_test, y_test) = mnist.load_data()
    img_rows, img_cols = X_train.shape[1], X_train.shape[2]
    X_train = (X_train.astype(np.float32) - 127.5) / 127.5
    X_train = X_train.reshape((X_train.shape[0], 1) + X_train.shape[1:])
    discriminator = discriminator_model()
    generator = generator_model()
    discriminator_on_generator = \
        generator_containing_discriminator(generator, discriminator)
    d_optim = SGD(lr=0.0005, momentum=0.9, nesterov=True)
    g_optim = SGD(lr=0.0005, momentum=0.9, nesterov=True)
    generator.compile(loss='binary_crossentropy', optimizer="SGD")
    discriminator_on_generator.compile(
        loss='binary_crossentropy', optimizer=g_optim)
    discriminator.trainable = True
    discriminator.compile(loss='binary_crossentropy', optimizer=d_optim)
    noise = np.zeros((BATCH_SIZE, 100))
    for epoch in range(100):
        print("Epoch is", epoch)
        print("Number of batches", int(X_train.shape[0] / BATCH_SIZE))
        start = timeit.default_timer()
        for index in range(int(X_train.shape[0] / BATCH_SIZE)):
            for i in range(BATCH_SIZE):
                noise[i, :] = np.random.uniform(-1, 1, 100)
            image_batch = X_train[index * BATCH_SIZE:(index + 1) * BATCH_SIZE]
            image_batch = image_batch.reshape(image_batch.shape[0], 
                                              image_batch.shape[2], 
                                              image_batch.shape[3],
                                              image_batch.shape[1])
            generated_images = generator.predict(noise, verbose=0)
            if index % 200 == 0:
                image = combine_images(generated_images)
                image = image * 127.5 + 127.5
                Image.fromarray(image.astype(np.uint8)).save(
                    str(epoch)+"_"+str(index)+".png")
            X = np.concatenate((image_batch, generated_images))
            y = [1] * BATCH_SIZE + [0] * BATCH_SIZE
            d_loss = discriminator.train_on_batch(X, y)
            print("batch %d d_loss : %f" % (index, d_loss))
            for i in range(BATCH_SIZE):
                noise[i, :] = np.random.uniform(-1, 1, 100)
            discriminator.trainable = False
            g_loss = discriminator_on_generator.train_on_batch(
                noise, [1] * BATCH_SIZE)
            discriminator.trainable = True
            print("batch %d g_loss : %f" % (index, g_loss))
            if index % 10 == 9:
                generator.save_weights('generator', True)
                discriminator.save_weights('discriminator', True)
        stop = timeit.default_timer()
        print('Epoch time calculate {0}'.format(stop - start)) 


# Image Generator

In [ ]:
def generate(BATCH_SIZE, nice=False):
    generator = generator_model()
    generator.compile(loss='binary_crossentropy', optimizer='SGD')
    generator.load_weights('generator')
    if nice:
        discriminator = discriminator_model()
        discriminator.compile(loss='binary_crossentropy', optimizer='SGD')
        discriminator.load_weights('discriminator')
        noise = np.zeros((BATCH_SIZE * 20, 100))
        for i in range(BATCH_SIZE * 20):
            noise[i, :] = np.random.uniform(-1, 1, 100)
        generated_images = generator.predict(noise, verbose=1)
        d_pret = discriminator.predict(generated_images, verbose=1)
        index = np.arrange(0, BATCH_SIZE * 20)
        index.resize((BATCH_SIZE * 20, 1))
        pre_with_index = list(np.append(d_pret, index, axis=1))
        pre_with_index.sort(key=lambda x: x[0], reverse=True)
        nice_images = np.zeros((BATCH_SIZE, 1) +
                              (generated_images.shape[2:]), dtype=np.float32)
        for i in range(int(BATCH_SIZE)):
            idx = int(pre_with_index[i][1])
            nice_images[i, 0, :, :] = generated_images[idx, 0, :, :]
        image = combine_images(nice_images)
    else:
        noise = np.zeros((BATCH_SIZE, 100))
        for i in range(BATCH_SIZE):
            noise[i, :] = np.random.uniform(-1, 1, 100)
        generated_images = generator.predict(noise, verbose=1)
        image = combine_images(generated_images)
    image = image * 127.5 + 127.5
    Image.fromarray(image.astype(np.uint8)).save('geneted_image.png')

# Training

In [127]:
train(BATCH_SIZE=100)

Epoch is 0
Number of batches 600
(100, 28, 28, 1)
(100, 1, 28, 28)
batch 0 d_loss : 0.678023
batch 0 g_loss : 0.620962
batch 1 d_loss : 0.667493
batch 1 g_loss : 0.617225
batch 2 d_loss : 0.662333
batch 2 g_loss : 0.615967
batch 3 d_loss : 0.649278
batch 3 g_loss : 0.611214
batch 4 d_loss : 0.628940
batch 4 g_loss : 0.602555
batch 5 d_loss : 0.615188
batch 5 g_loss : 0.599596
batch 6 d_loss : 0.597353
batch 6 g_loss : 0.589336
batch 7 d_loss : 0.580325
batch 7 g_loss : 0.587567
batch 8 d_loss : 0.565466
batch 8 g_loss : 0.582442
batch 9 d_loss : 0.544886
batch 9 g_loss : 0.573681
batch 10 d_loss : 0.529137
batch 10 g_loss : 0.572061
batch 11 d_loss : 0.515028
batch 11 g_loss : 0.567133
batch 12 d_loss : 0.511801
batch 12 g_loss : 0.565002
batch 13 d_loss : 0.502310
batch 13 g_loss : 0.556129
batch 14 d_loss : 0.486091
batch 14 g_loss : 0.556396
batch 15 d_loss : 0.475228
batch 15 g_loss : 0.552154
batch 16 d_loss : 0.466723
batch 16 g_loss : 0.550734
batch 17 d_loss : 0.461204
batch 17

batch 149 g_loss : 0.901970
batch 150 d_loss : 0.254205
batch 150 g_loss : 0.958360
batch 151 d_loss : 0.273919
batch 151 g_loss : 0.985202
batch 152 d_loss : 0.252804
batch 152 g_loss : 1.003768
batch 153 d_loss : 0.246475
batch 153 g_loss : 1.070273
batch 154 d_loss : 0.257525
batch 154 g_loss : 1.135477
batch 155 d_loss : 0.250439
batch 155 g_loss : 1.128028
batch 156 d_loss : 0.226595
batch 156 g_loss : 1.162930
batch 157 d_loss : 0.219421
batch 157 g_loss : 1.235137
batch 158 d_loss : 0.211213
batch 158 g_loss : 1.275650
batch 159 d_loss : 0.201294
batch 159 g_loss : 1.295279
batch 160 d_loss : 0.184199
batch 160 g_loss : 1.299959
batch 161 d_loss : 0.186177
batch 161 g_loss : 1.383102
batch 162 d_loss : 0.177423
batch 162 g_loss : 1.394972
batch 163 d_loss : 0.182041
batch 163 g_loss : 1.475083
batch 164 d_loss : 0.179217
batch 164 g_loss : 1.529371
batch 165 d_loss : 0.179137
batch 165 g_loss : 1.531397
batch 166 d_loss : 0.177038
batch 166 g_loss : 1.563636
batch 167 d_loss : 0

batch 295 g_loss : 1.097683
batch 296 d_loss : 0.533109
batch 296 g_loss : 1.137199
batch 297 d_loss : 0.513381
batch 297 g_loss : 1.104103
batch 298 d_loss : 0.541741
batch 298 g_loss : 1.074206
batch 299 d_loss : 0.558824
batch 299 g_loss : 1.051316
batch 300 d_loss : 0.509782
batch 300 g_loss : 1.060855
batch 301 d_loss : 0.558398
batch 301 g_loss : 1.046324
batch 302 d_loss : 0.533188
batch 302 g_loss : 1.028618
batch 303 d_loss : 0.512576
batch 303 g_loss : 1.042942
batch 304 d_loss : 0.485752
batch 304 g_loss : 1.053735
batch 305 d_loss : 0.500370
batch 305 g_loss : 1.060761
batch 306 d_loss : 0.515019
batch 306 g_loss : 1.072896
batch 307 d_loss : 0.530746
batch 307 g_loss : 1.121132
batch 308 d_loss : 0.483973
batch 308 g_loss : 1.087032
batch 309 d_loss : 0.479628
batch 309 g_loss : 1.127911
batch 310 d_loss : 0.501371
batch 310 g_loss : 1.117367
batch 311 d_loss : 0.561930
batch 311 g_loss : 1.128131
batch 312 d_loss : 0.544300
batch 312 g_loss : 1.074780
batch 313 d_loss : 0

batch 441 g_loss : 1.034383
batch 442 d_loss : 0.513450
batch 442 g_loss : 1.021737
batch 443 d_loss : 0.513143
batch 443 g_loss : 1.004292
batch 444 d_loss : 0.537557
batch 444 g_loss : 1.034433
batch 445 d_loss : 0.536569
batch 445 g_loss : 1.043880
batch 446 d_loss : 0.488333
batch 446 g_loss : 0.989400
batch 447 d_loss : 0.531230
batch 447 g_loss : 1.010615
batch 448 d_loss : 0.550457
batch 448 g_loss : 1.044495
batch 449 d_loss : 0.552536
batch 449 g_loss : 1.026652
batch 450 d_loss : 0.531160
batch 450 g_loss : 1.060375
batch 451 d_loss : 0.565580
batch 451 g_loss : 0.996234
batch 452 d_loss : 0.576213
batch 452 g_loss : 0.989708
batch 453 d_loss : 0.538175
batch 453 g_loss : 0.961190
batch 454 d_loss : 0.515917
batch 454 g_loss : 1.040607
batch 455 d_loss : 0.533134
batch 455 g_loss : 1.016175
batch 456 d_loss : 0.538157
batch 456 g_loss : 1.017353
batch 457 d_loss : 0.553304
batch 457 g_loss : 1.046499
batch 458 d_loss : 0.502078
batch 458 g_loss : 1.071884
batch 459 d_loss : 0

batch 588 d_loss : 0.454087
batch 588 g_loss : 1.118105
batch 589 d_loss : 0.419836
batch 589 g_loss : 1.186919
batch 590 d_loss : 0.431868
batch 590 g_loss : 1.227271
batch 591 d_loss : 0.420764
batch 591 g_loss : 1.230667
batch 592 d_loss : 0.428446
batch 592 g_loss : 1.250205
batch 593 d_loss : 0.457664
batch 593 g_loss : 1.237000
batch 594 d_loss : 0.503121
batch 594 g_loss : 1.356398
batch 595 d_loss : 0.447000
batch 595 g_loss : 1.315988
batch 596 d_loss : 0.486974
batch 596 g_loss : 1.271585
batch 597 d_loss : 0.489734
batch 597 g_loss : 1.072518
batch 598 d_loss : 0.445891
batch 598 g_loss : 1.155688
batch 599 d_loss : 0.597094
batch 599 g_loss : 1.029948
Epoch time calculate 837.2995466669963
Epoch is 1
Number of batches 600
(100, 28, 28, 1)
(100, 1, 28, 28)
batch 0 d_loss : 0.474808
batch 0 g_loss : 0.966448
batch 1 d_loss : 0.469595
batch 1 g_loss : 0.995308
batch 2 d_loss : 0.499813
batch 2 g_loss : 1.045759
batch 3 d_loss : 0.431479
batch 3 g_loss : 1.188738
batch 4 d_loss

...

batch 488 g_loss : 2.028592
batch 489 d_loss : 0.177603
batch 489 g_loss : 2.553658
batch 490 d_loss : 0.167275
batch 490 g_loss : 2.784425
batch 491 d_loss : 0.263477
batch 491 g_loss : 1.954119
batch 492 d_loss : 0.257071
batch 492 g_loss : 2.947404
batch 493 d_loss : 0.323423
batch 493 g_loss : 1.872527
batch 494 d_loss : 0.240395
batch 494 g_loss : 3.539397
batch 495 d_loss : 0.217845
batch 495 g_loss : 2.938221
batch 496 d_loss : 0.226502
batch 496 g_loss : 2.659654
batch 497 d_loss : 0.184512
batch 497 g_loss : 2.503766
batch 498 d_loss : 0.233281
batch 498 g_loss : 2.911224
batch 499 d_loss : 0.188750
batch 499 g_loss : 1.933058
batch 500 d_loss : 0.254256
batch 500 g_loss : 2.833817
batch 501 d_loss : 0.240931
batch 501 g_loss : 3.230513
batch 502 d_loss : 0.243618
batch 502 g_loss : 2.550870
batch 503 d_loss : 0.215048
batch 503 g_loss : 2.179337
batch 504 d_loss : 0.191299
batch 504 g_loss : 2.040811
batch 505 d_loss : 0.240186
batch 505 g_loss : 2.894746
batch 506 d_loss : 0

batch 34 g_loss : 2.583918
batch 35 d_loss : 0.232380
batch 35 g_loss : 1.912708
batch 36 d_loss : 0.218098
batch 36 g_loss : 2.401080
batch 37 d_loss : 0.246873
batch 37 g_loss : 2.833694
batch 38 d_loss : 0.170898
batch 38 g_loss : 2.629330
batch 39 d_loss : 0.195037
batch 39 g_loss : 2.958813
batch 40 d_loss : 0.225724
batch 40 g_loss : 2.312135
batch 41 d_loss : 0.273520
batch 41 g_loss : 2.634738
batch 42 d_loss : 0.216820
batch 42 g_loss : 2.526125
batch 43 d_loss : 0.165576
batch 43 g_loss : 3.334517
batch 44 d_loss : 0.220736
batch 44 g_loss : 2.508845
batch 45 d_loss : 0.233442
batch 45 g_loss : 2.257242
batch 46 d_loss : 0.196719
batch 46 g_loss : 2.513543
batch 47 d_loss : 0.228939
batch 47 g_loss : 2.505771
batch 48 d_loss : 0.219815
batch 48 g_loss : 2.249691
batch 49 d_loss : 0.277632
batch 49 g_loss : 2.294042
batch 50 d_loss : 0.234036
batch 50 g_loss : 2.377297
batch 51 d_loss : 0.232355
batch 51 g_loss : 2.319669
batch 52 d_loss : 0.230608
batch 52 g_loss : 2.003093
b

batch 183 g_loss : 2.529669
batch 184 d_loss : 0.222120
batch 184 g_loss : 2.704431
batch 185 d_loss : 0.184930
batch 185 g_loss : 2.736558
batch 186 d_loss : 0.166252
batch 186 g_loss : 2.679654
batch 187 d_loss : 0.221814
batch 187 g_loss : 3.193945
batch 188 d_loss : 0.271461
batch 188 g_loss : 2.244205
batch 189 d_loss : 0.205308
batch 189 g_loss : 2.716674
batch 190 d_loss : 0.185900
batch 190 g_loss : 2.627772
batch 191 d_loss : 0.185941
batch 191 g_loss : 2.874733
batch 192 d_loss : 0.229782
batch 192 g_loss : 2.114855
batch 193 d_loss : 0.229674
batch 193 g_loss : 3.101835
batch 194 d_loss : 0.319618
batch 194 g_loss : 2.048917
batch 195 d_loss : 0.309262
batch 195 g_loss : 2.634658
batch 196 d_loss : 0.268817
batch 196 g_loss : 1.889949
batch 197 d_loss : 0.319959
batch 197 g_loss : 3.396981
batch 198 d_loss : 0.296250
batch 198 g_loss : 2.126414
batch 199 d_loss : 0.200179
batch 199 g_loss : 1.981761
(100, 28, 28, 1)
(100, 1, 28, 28)
batch 200 d_loss : 0.247664
batch 200 g_lo

batch 329 g_loss : 2.902840
batch 330 d_loss : 0.243780
batch 330 g_loss : 2.138333
batch 331 d_loss : 0.222637
batch 331 g_loss : 2.004061
batch 332 d_loss : 0.210066
batch 332 g_loss : 3.186085
batch 333 d_loss : 0.250010
batch 333 g_loss : 2.264832
batch 334 d_loss : 0.220860
batch 334 g_loss : 2.060816
batch 335 d_loss : 0.223408
batch 335 g_loss : 2.453439
batch 336 d_loss : 0.262604
batch 336 g_loss : 2.195217
batch 337 d_loss : 0.227512
batch 337 g_loss : 2.321100
batch 338 d_loss : 0.228564
batch 338 g_loss : 2.469442
batch 339 d_loss : 0.206781
batch 339 g_loss : 2.574729
batch 340 d_loss : 0.182149
batch 340 g_loss : 2.883784
batch 341 d_loss : 0.168193
batch 341 g_loss : 3.144563
batch 342 d_loss : 0.207194
batch 342 g_loss : 2.450919
batch 343 d_loss : 0.223345
batch 343 g_loss : 2.409213
batch 344 d_loss : 0.202888
batch 344 g_loss : 2.425779
batch 345 d_loss : 0.253231
batch 345 g_loss : 1.963414
batch 346 d_loss : 0.241989
batch 346 g_loss : 2.632577
batch 347 d_loss : 0

batch 475 g_loss : 2.161510
batch 476 d_loss : 0.263737
batch 476 g_loss : 3.177933
batch 477 d_loss : 0.279268
batch 477 g_loss : 1.910317
batch 478 d_loss : 0.187939
batch 478 g_loss : 2.661569
batch 479 d_loss : 0.274774
batch 479 g_loss : 1.729962
batch 480 d_loss : 0.272697
batch 480 g_loss : 2.952799
batch 481 d_loss : 0.319170
batch 481 g_loss : 1.614638
batch 482 d_loss : 0.322132
batch 482 g_loss : 3.620767
batch 483 d_loss : 0.295884
batch 483 g_loss : 1.993547
batch 484 d_loss : 0.228204
batch 484 g_loss : 2.354657
batch 485 d_loss : 0.224527
batch 485 g_loss : 2.184778
batch 486 d_loss : 0.245622
batch 486 g_loss : 2.220698
batch 487 d_loss : 0.266297
batch 487 g_loss : 2.289591
batch 488 d_loss : 0.227131
batch 488 g_loss : 1.878115
batch 489 d_loss : 0.238378
batch 489 g_loss : 3.220286
batch 490 d_loss : 0.183467
batch 490 g_loss : 2.431465
batch 491 d_loss : 0.246903
batch 491 g_loss : 1.895686
batch 492 d_loss : 0.237880
batch 492 g_loss : 2.690034
batch 493 d_loss : 0